# Exploratory Data Analysis (EDA) - Calorie Prediction

This notebook performs comprehensive exploratory data analysis on the calorie prediction dataset.

## Goals:
1. Load train/test datasets
2. Generate ydata-profiling report
3. Validate basic assumptions
4. Domain-driven feature exploration
5. Outlier diagnostics
6. Scaling preview
7. Correlation and multicollinearity analysis
8. Save artifacts and summary

In [1]:
# Cell 0: Package installation guard
import subprocess
import sys


In [ ]:

required_packages = ['ydata-profiling', 'statsmodels']

for package in required_packages:
    try:
        if package == 'ydata-profiling':
            import ydata_profiling
        elif package == 'statsmodels':
            import statsmodels
        print(f"✓ {package} already installed")
    except ImportError:
        print(f"Installing {package}...")
        subprocess.check_call([sys.executable, '-m', 'pip', 'install', package])

In [1]:
# Cell 1: Imports and paths
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from ydata_profiling import ProfileReport
from statsmodels.stats.outliers_influence import variance_inflation_factor
from sklearn.preprocessing import StandardScaler
from scipy import stats
import warnings
warnings.filterwarnings('ignore')

# Import config
import sys
sys.path.append('../src')
from config import (
    DATA_RAW, DATA_PROCESSED, REPORTS_DIR,
    RAW_NUM_FEATURES, TARGET_COL, CAT_COL, DERIVED_FEATURES
)

# Set display options
pd.set_option('display.max_columns', None)
plt.style.use('default')
sns.set_palette("husl")

print(f"Data path: {DATA_RAW}")
print(f"Reports path: {REPORTS_DIR}")

Data path: /Users/omarhassan/Desktop/calorie competition/data/raw
Reports path: /Users/omarhassan/Desktop/calorie competition/reports


In [2]:
# Cell 2: Load CSVs and basic info
print("Loading datasets...")
train_df = pd.read_csv(DATA_RAW / 'train.csv')
test_df = pd.read_csv(DATA_RAW / 'test.csv')

print(f"Train shape: {train_df.shape}")
print(f"Test shape: {test_df.shape}")

print("\n=== TRAIN DATASET INFO ===")
print(train_df.info())
print("\nFirst 5 rows:")
display(train_df.head())

print("\n=== TEST DATASET INFO ===")
print(test_df.info())
print("\nFirst 5 rows:")
display(test_df.head())

print(f"\nTrain columns: {list(train_df.columns)}")
print(f"Test columns: {list(test_df.columns)}")
print(f"\nExpected raw features: {RAW_NUM_FEATURES}")
print(f"Target column: {TARGET_COL}")
print(f"Categorical column: {CAT_COL}")

Loading datasets...
Train shape: (750000, 9)
Test shape: (250000, 8)

=== TRAIN DATASET INFO ===
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 750000 entries, 0 to 749999
Data columns (total 9 columns):
 #   Column      Non-Null Count   Dtype  
---  ------      --------------   -----  
 0   id          750000 non-null  int64  
 1   Sex         750000 non-null  object 
 2   Age         750000 non-null  int64  
 3   Height      750000 non-null  float64
 4   Weight      750000 non-null  float64
 5   Duration    750000 non-null  float64
 6   Heart_Rate  750000 non-null  float64
 7   Body_Temp   750000 non-null  float64
 8   Calories    750000 non-null  float64
dtypes: float64(6), int64(2), object(1)
memory usage: 51.5+ MB
None

First 5 rows:


id     Sex  Age  Height  Weight  Duration  Heart_Rate  Body_Temp  Calories
0   0    male   36   189.0    82.0      26.0       101.0       41.0     150.0
1   1  female   64   163.0    60.0       8.0        85.0       39.7      34.0
2   2  female   51   161.0    64.0       7.0        84.0       39.8      29.0
3   3    male   20   192.0    90.0      25.0       105.0       40.7     140.0
4   4  female   38   166.0    61.0      25.0       102.0       40.6     146.0


=== TEST DATASET INFO ===
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 250000 entries, 0 to 249999
Data columns (total 8 columns):
 #   Column      Non-Null Count   Dtype  
---  ------      --------------   -----  
 0   id          250000 non-null  int64  
 1   Sex         250000 non-null  object 
 2   Age         250000 non-null  int64  
 3   Height      250000 non-null  float64
 4   Weight      250000 non-null  float64
 5   Duration    250000 non-null  float64
 6   Heart_Rate  250000 non-null  float64
 7   Body_Temp   250000 non-null  float64
dtypes: float64(5), int64(2), object(1)
memory usage: 15.3+ MB
None

First 5 rows:


id     Sex  Age  Height  Weight  Duration  Heart_Rate  Body_Temp
0  750000    male   45   177.0    81.0       7.0        87.0       39.8
1  750001    male   26   200.0    97.0      20.0       101.0       40.5
2  750002  female   29   188.0    85.0      16.0       102.0       40.4
3  750003  female   39   172.0    73.0      20.0       107.0       40.6
4  750004  female   30   173.0    67.0      16.0        94.0       40.5


Train columns: ['id', 'Sex', 'Age', 'Height', 'Weight', 'Duration', 'Heart_Rate', 'Body_Temp', 'Calories']
Test columns: ['id', 'Sex', 'Age', 'Height', 'Weight', 'Duration', 'Heart_Rate', 'Body_Temp']

Expected raw features: ['Age', 'Height', 'Weight', 'Duration', 'Heart_Rate', 'Body_Temp']
Target column: Calories
Categorical column: Sex


## 2. YData Profiling Report Generation

In [3]:
# Generate ydata-profiling report
print("Generating ydata-profiling report...")
profile = ProfileReport(
    train_df, 
    title="Calorie Prediction Dataset - EDA Report",
    explorative=True,
    minimal=False
)

# Save report
report_path = REPORTS_DIR / 'eda_profile.html'
profile.to_file(report_path)
print(f"✓ Report saved to: {report_path}")

# Display in notebook (optional)
profile.to_notebook_iframe()

Generating ydata-profiling report...


Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

100%|██████████| 9/9 [00:00<00:00, 11.91it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

✓ Report saved to: /Users/omarhassan/Desktop/calorie competition/reports/eda_profile.html


## 3. Basic Assumptions Validation

In [ ]:
# Cell 3: Basic assumptions validation
print("=== BASIC ASSUMPTIONS VALIDATION ===")

# Column types & unique counts
print("\n1. COLUMN TYPES & UNIQUE COUNTS:")
for col in train_df.columns:
    dtype = train_df[col].dtype
    unique_count = train_df[col].nunique()
    print(f"{col:15} | {str(dtype):10} | {unique_count:6} unique values")

# Target distribution & outliers
print("\n2. TARGET (Calories) DISTRIBUTION:")
calories = train_df[TARGET_COL]
print(f"Mean: {calories.mean():.2f}")
print(f"Median: {calories.median():.2f}")
print(f"Std: {calories.std():.2f}")
print(f"Min: {calories.min():.2f}")
print(f"Max: {calories.max():.2f}")
print(f"Skewness: {calories.skew():.3f}")
print(f"Kurtosis: {calories.kurtosis():.3f}")

# Outlier detection using IQR
Q1 = calories.quantile(0.25)
Q3 = calories.quantile(0.75)
IQR = Q3 - Q1
lower_bound = Q1 - 1.5 * IQR
upper_bound = Q3 + 1.5 * IQR
outliers = calories[(calories < lower_bound) | (calories > upper_bound)]
print(f"IQR outliers: {len(outliers)} ({len(outliers)/len(calories)*100:.1f}%)")

# Plot target distribution
fig, axes = plt.subplots(1, 2, figsize=(12, 4))
axes[0].hist(calories, bins=50, alpha=0.7, color='skyblue', edgecolor='black')
axes[0].set_title('Calories Distribution')
axes[0].set_xlabel('Calories')
axes[0].set_ylabel('Frequency')

axes[1].boxplot(calories)
axes[1].set_title('Calories Boxplot')
axes[1].set_ylabel('Calories')
plt.tight_layout()
plt.show()

# Sex balance
print("\n3. SEX BALANCE:")
sex_counts = train_df[CAT_COL].value_counts()
sex_props = train_df[CAT_COL].value_counts(normalize=True) * 100
print(sex_counts)
print(f"Proportions: {dict(sex_props.round(1))}")
expected_50_50 = abs(sex_props['male'] - 50) < 5 and abs(sex_props['female'] - 50) < 5
print(f"Approximately 50/50 balance: {expected_50_50}")

# Missing values audit
print("\n4. MISSING VALUES AUDIT:")
missing_train = train_df.isnull().sum()
missing_test = test_df.isnull().sum()
print("Train missing values:")
print(missing_train[missing_train > 0] if missing_train.sum() > 0 else "No missing values")
print("Test missing values:")
print(missing_test[missing_test > 0] if missing_test.sum() > 0 else "No missing values")

total_missing = missing_train.sum() + missing_test.sum()
print(f"\nZero missing values expected: {total_missing == 0}")

=== BASIC ASSUMPTIONS VALIDATION ===

1. COLUMN TYPES & UNIQUE COUNTS:
id              | int64      | 750000 unique values
Sex             | object     |      2 unique values
Age             | int64      |     60 unique values
Height          | float64    |     86 unique values
Weight          | float64    |     91 unique values
Duration        | float64    |     30 unique values
Heart_Rate      | float64    |     63 unique values
Body_Temp       | float64    |     75 unique values
Calories        | float64    |    277 unique values

2. TARGET (Calories) DISTRIBUTION:
Mean: 88.28
Median: 77.00
Std: 62.40
Min: 1.00
Max: 314.00
Skewness: 0.539
Kurtosis: -0.690
IQR outliers: 139 (0.0%)

3. SEX BALANCE:
Sex
female    375721
male      374279
Name: count, dtype: int64
Proportions: {'female': 50.1, 'male': 49.9}
✓ Approximately 50/50 balance: True

4. MISSING VALUES AUDIT:
Train missing values:
No missing values
Test missing values:
No missing values

Zero missing values expected: True


## 4. Domain-Driven Feature Exploration

In [6]:
# Cell 4: Domain-driven feature exploration
print("=== DOMAIN-DRIVEN FEATURE EXPLORATION ===")

# Create derived features
def create_derived_features(df):
    df_new = df.copy()
    
    # BMI = Weight / (Height_m²)
    height_m = df_new['Height'] / 100
    df_new['BMI'] = df_new['Weight'] / (height_m ** 2)
    
    # HRxDur = Heart_Rate × Duration
    df_new['HRxDur'] = df_new['Heart_Rate'] * df_new['Duration']
    
    # Age_x_BodyTemp = Age × Body_Temp
    df_new['Age_x_BodyTemp'] = df_new['Age'] * df_new['Body_Temp']
    
    # HeatStressIdx = Body_Temp × Heart_Rate / 100
    df_new['HeatStressIdx'] = df_new['Body_Temp'] * df_new['Heart_Rate'] / 100
    
    return df_new

# Create features for train set
train_enhanced = create_derived_features(train_df)
print("Derived features created:")
for feat in DERIVED_FEATURES:
    print(f"  - {feat}: mean={train_enhanced[feat].mean():.2f}, std={train_enhanced[feat].std():.2f}")

# Plot distributions of derived features
fig, axes = plt.subplots(2, 2, figsize=(12, 8))
axes = axes.ravel()

for i, feat in enumerate(DERIVED_FEATURES):
    axes[i].hist(train_enhanced[feat], bins=30, alpha=0.7, color=f'C{i}', edgecolor='black')
    axes[i].set_title(f'{feat} Distribution')
    axes[i].set_xlabel(feat)
    axes[i].set_ylabel('Frequency')

plt.tight_layout()
plt.show()

# Correlation with target
print("\nCORRELATION WITH TARGET (Calories):")
all_numeric_features = RAW_NUM_FEATURES + DERIVED_FEATURES
correlations = train_enhanced[all_numeric_features + [TARGET_COL]].corr()[TARGET_COL].drop(TARGET_COL)
correlations_sorted = correlations.abs().sort_values(ascending=False)

print("Top correlations with Calories:")
for feat, corr in correlations_sorted.head(10).items():
    original_corr = correlations[feat]
    print(f"{feat:15} | {original_corr:6.3f} (|{corr:.3f}|)")

# Plot correlation with target
plt.figure(figsize=(10, 6))
correlations_sorted.plot(kind='barh')
plt.title('Absolute Correlation with Calories (Target)')
plt.xlabel('Absolute Correlation')
plt.tight_layout()
plt.show()

# Variance Inflation Factor (VIF)
print("\nVARIANCE INFLATION FACTOR (VIF):")
numeric_data = train_enhanced[all_numeric_features].fillna(0)

vif_data = pd.DataFrame()
vif_data["Feature"] = numeric_data.columns
vif_data["VIF"] = [variance_inflation_factor(numeric_data.values, i) 
                   for i in range(numeric_data.shape[1])]

vif_data = vif_data.sort_values('VIF', ascending=False)
print(vif_data.to_string(index=False))

high_vif = vif_data[vif_data['VIF'] > 10]
if len(high_vif) > 0:
    print(f"\nHigh VIF (>10) features: {len(high_vif)}")
    print(high_vif.to_string(index=False))
else:
    print("\nNo high VIF (>10) features detected")

=== DOMAIN-DRIVEN FEATURE EXPLORATION ===
Derived features created:
  - BMI: mean=24.37, std=1.51
  - HRxDur: mean=1541.56, std=932.45
  - Age_x_BodyTemp: mean=1658.68, std=609.75
  - HeatStressIdx: mean=38.29, std=4.38

CORRELATION WITH TARGET (Calories):
Top correlations with Calories:
HRxDur          |  0.977 (|0.977|)
Duration        |  0.960 (|0.960|)
HeatStressIdx   |  0.925 (|0.925|)
Heart_Rate      |  0.909 (|0.909|)
Body_Temp       |  0.829 (|0.829|)
Age_x_BodyTemp  |  0.190 (|0.190|)
Age             |  0.146 (|0.146|)
BMI             |  0.049 (|0.049|)
Weight          |  0.016 (|0.016|)
Height          | -0.004 (|0.004|)

VARIANCE INFLATION FACTOR (VIF):
       Feature          VIF
 HeatStressIdx 80460.533132
    Heart_Rate 79908.011049
     Body_Temp 33363.215499
        Height 31112.530427
           Age 22001.303550
Age_x_BodyTemp 21998.977448
        Weight  7996.781441
           BMI  7924.101832
      Duration  1015.140724
        HRxDur   930.783028

High VIF (>10) fea

## 5. Outlier Diagnostics

In [7]:
# Cell 5: Outlier diagnostics
print("=== OUTLIER DIAGNOSTICS ===")

# Plot box-whisker plots for all numeric features
n_features = len(RAW_NUM_FEATURES)
n_cols = 3
n_rows = (n_features + n_cols - 1) // n_cols

fig, axes = plt.subplots(n_rows, n_cols, figsize=(15, 4*n_rows))
if n_rows == 1:
    axes = axes.reshape(1, -1)
axes = axes.flatten()

outlier_summary = []

for i, feature in enumerate(RAW_NUM_FEATURES):
    data = train_enhanced[feature]
    
    # Box plot
    axes[i].boxplot(data, patch_artist=True)
    axes[i].set_title(f'{feature} - Outlier Detection')
    axes[i].set_ylabel(feature)
    
    # Calculate quantiles and outlier limits
    q_0_5 = data.quantile(0.005)
    q_99_5 = data.quantile(0.995)
    q1 = data.quantile(0.25)
    q3 = data.quantile(0.75)
    iqr = q3 - q1
    iqr_lower = q1 - 1.5 * iqr
    iqr_upper = q3 + 1.5 * iqr
    
    # Count outliers
    iqr_outliers = len(data[(data < iqr_lower) | (data > iqr_upper)])
    quantile_outliers = len(data[(data < q_0_5) | (data > q_99_5)])
    
    outlier_summary.append({
        'feature': feature,
        'q_0.5%': q_0_5,
        'q_99.5%': q_99_5,
        'iqr_outliers': iqr_outliers,
        'quantile_outliers': quantile_outliers,
        'winsor_lower': q_0_5,
        'winsor_upper': q_99_5
    })

# Hide unused subplots
for i in range(len(RAW_NUM_FEATURES), len(axes)):
    axes[i].set_visible(False)

plt.tight_layout()
plt.savefig(REPORTS_DIR / 'outlier_boxplots.png', dpi=300, bbox_inches='tight')
plt.show()

# Print outlier summary
print("\nOUTLIER SUMMARY:")
outlier_df = pd.DataFrame(outlier_summary)
print(outlier_df.to_string(index=False, float_format='%.3f'))

print("\nRECOMMENDED WINSORIZATION LIMITS (0.5% tails):")
for _, row in outlier_df.iterrows():
    print(f"{row['feature']:15} | Lower: {row['winsor_lower']:8.3f} | Upper: {row['winsor_upper']:8.3f}")

# Decision on winsorization
total_outliers = outlier_df['quantile_outliers'].sum()
total_samples = len(train_enhanced)
outlier_rate = total_outliers / total_samples * 100

print(f"\nTotal outliers (0.5%/99.5% quantiles): {total_outliers} ({outlier_rate:.1f}% of data)")
winsorize_recommended = outlier_rate > 2.0
print(f"Winsorization recommended: {winsorize_recommended} (threshold: >2% outliers)")

=== OUTLIER DIAGNOSTICS ===

OUTLIER SUMMARY:
   feature  q_0.5%  q_99.5%  iqr_outliers  quantile_outliers  winsor_lower  winsor_upper
       Age  20.000   79.000             0                  0        20.000        79.000
    Height 148.000  203.000            14               5536       148.000       203.000
    Weight  50.000  104.000             9               5541        50.000       104.000
  Duration   1.000   30.000             0                  0         1.000        30.000
Heart_Rate  74.000  116.000            36               5923        74.000       116.000
 Body_Temp  37.700   41.200         14919               5018        37.700        41.200

RECOMMENDED WINSORIZATION LIMITS (0.5% tails):
Age             | Lower:   20.000 | Upper:   79.000
Height          | Lower:  148.000 | Upper:  203.000
Weight          | Lower:   50.000 | Upper:  104.000
Duration        | Lower:    1.000 | Upper:   30.000
Heart_Rate      | Lower:   74.000 | Upper:  116.000
Body_Temp       | Lower

## 6. Scaling Preview

In [8]:
# Cell 6: Scaling preview
print("=== SCALING PREVIEW ===")

# Prepare data for scaling
features_to_scale = RAW_NUM_FEATURES + DERIVED_FEATURES
data_to_scale = train_enhanced[features_to_scale].copy()

# Apply StandardScaler
scaler = StandardScaler()
data_scaled = pd.DataFrame(
    scaler.fit_transform(data_to_scale),
    columns=data_to_scale.columns,
    index=data_to_scale.index
)

print("Standard Scaling Applied:")
print(f"Original data shape: {data_to_scale.shape}")
print(f"Scaled data shape: {data_scaled.shape}")

# Before/after comparison for BMI and HRxDur
comparison_features = ['BMI', 'HRxDur']

fig, axes = plt.subplots(2, 2, figsize=(12, 8))

for i, feature in enumerate(comparison_features):
    # Before scaling
    axes[i, 0].hist(data_to_scale[feature], bins=30, alpha=0.7, color='lightblue', edgecolor='black')
    axes[i, 0].set_title(f'{feature} - Before Scaling')
    axes[i, 0].set_xlabel(feature)
    axes[i, 0].set_ylabel('Frequency')
    
    # After scaling
    axes[i, 1].hist(data_scaled[feature], bins=30, alpha=0.7, color='lightcoral', edgecolor='black')
    axes[i, 1].set_title(f'{feature} - After Scaling')
    axes[i, 1].set_xlabel(f'{feature} (scaled)')
    axes[i, 1].set_ylabel('Frequency')

plt.tight_layout()
plt.show()

# Statistics comparison
print("\nSCALING STATISTICS COMPARISON:")
print("\nBefore Scaling:")
print(data_to_scale[comparison_features].describe().round(3))

print("\nAfter Scaling:")
print(data_scaled[comparison_features].describe().round(3))

# Verify scaling properties
print("\nSCALING VERIFICATION:")
for feature in comparison_features:
    mean_scaled = data_scaled[feature].mean()
    std_scaled = data_scaled[feature].std()
    print(f"{feature:10} | Mean: {mean_scaled:6.3f} | Std: {std_scaled:6.3f}")

scaling_correct = all(abs(data_scaled[feat].mean()) < 1e-10 and abs(data_scaled[feat].std() - 1) < 1e-10 
                     for feat in features_to_scale)
print(f"\nStandard scaling correct (mean≈0, std≈1): {scaling_correct}")

=== SCALING PREVIEW ===
Standard Scaling Applied:
Original data shape: (750000, 10)
Scaled data shape: (750000, 10)

SCALING STATISTICS COMPARISON:

Before Scaling:
              BMI      HRxDur
count  750000.000  750000.000
mean       24.375    1541.563
std         1.511     932.453
min        12.376      67.000
25%        23.255     728.000
50%        24.391    1455.000
75%        25.488    2323.000
max        46.444    3840.000

After Scaling:
              BMI      HRxDur
count  750000.000  750000.000
mean       -0.000       0.000
std         1.000       1.000
min        -7.939      -1.581
25%        -0.741      -0.872
50%         0.011      -0.093
75%         0.736       0.838
max        14.603       2.465

SCALING VERIFICATION:
BMI        | Mean: -0.000 | Std:  1.000
HRxDur     | Mean:  0.000 | Std:  1.000

Standard scaling correct (mean≈0, std≈1): False


## 7. Correlation & Multicollinearity Analysis

In [9]:
# Cell 7: Correlation and multicollinearity
print("=== CORRELATION & MULTICOLLINEARITY ANALYSIS ===")

# Prepare correlation data
corr_features = RAW_NUM_FEATURES + DERIVED_FEATURES + [TARGET_COL]
corr_data = train_enhanced[corr_features]

# Calculate Pearson and Spearman correlations
pearson_corr = corr_data.corr(method='pearson')
spearman_corr = corr_data.corr(method='spearman')

print("Correlation matrices calculated:")
print(f"Pearson correlation shape: {pearson_corr.shape}")
print(f"Spearman correlation shape: {spearman_corr.shape}")

# Create correlation heatmaps
fig, axes = plt.subplots(1, 2, figsize=(20, 8))

# Pearson correlation heatmap
sns.heatmap(pearson_corr, annot=True, cmap='RdBu_r', center=0, 
            square=True, fmt='.2f', cbar_kws={'shrink': 0.8}, ax=axes[0])
axes[0].set_title('Pearson Correlation Matrix', fontsize=14)

# Spearman correlation heatmap
sns.heatmap(spearman_corr, annot=True, cmap='RdBu_r', center=0, 
            square=True, fmt='.2f', cbar_kws={'shrink': 0.8}, ax=axes[1])
axes[1].set_title('Spearman Correlation Matrix', fontsize=14)

plt.tight_layout()
plt.savefig(REPORTS_DIR / 'corr_heatmap.png', dpi=300, bbox_inches='tight')
plt.show()

# Find high correlations (|ρ| > 0.9)
def find_high_correlations(corr_matrix, threshold=0.9, method_name=""):
    high_corr_pairs = []
    
    for i in range(len(corr_matrix.columns)):
        for j in range(i+1, len(corr_matrix.columns)):
            corr_val = corr_matrix.iloc[i, j]
            if abs(corr_val) > threshold:
                high_corr_pairs.append({
                    'feature1': corr_matrix.columns[i],
                    'feature2': corr_matrix.columns[j],
                    'correlation': corr_val,
                    'abs_correlation': abs(corr_val),
                    'method': method_name
                })
    
    return sorted(high_corr_pairs, key=lambda x: x['abs_correlation'], reverse=True)

pearson_high = find_high_correlations(pearson_corr, 0.9, "Pearson")
spearman_high = find_high_correlations(spearman_corr, 0.9, "Spearman")

print("\nHIGH CORRELATIONS (|ρ| > 0.9):")

if pearson_high:
    print("\nPearson correlations > 0.9:")
    for pair in pearson_high:
        print(f"{pair['feature1']:15} <-> {pair['feature2']:15} | {pair['correlation']:6.3f}")
else:
    print("\nNo Pearson correlations > 0.9")

if spearman_high:
    print("\nSpearman correlations > 0.9:")
    for pair in spearman_high:
        print(f"{pair['feature1']:15} <-> {pair['feature2']:15} | {pair['correlation']:6.3f}")
else:
    print("\nNo Spearman correlations > 0.9")

# Recommendations for highly correlated pairs
all_high_corr = pearson_high + spearman_high
if all_high_corr:
    print("\nRECOMMENDATIONS FOR HIGHLY CORRELATED PAIRS:")
    unique_pairs = {}
    for pair in all_high_corr:
        key = tuple(sorted([pair['feature1'], pair['feature2']]))
        if key not in unique_pairs or abs(pair['correlation']) > abs(unique_pairs[key]['correlation']):
            unique_pairs[key] = pair
    
    for pair in unique_pairs.values():
        # Simple recommendation logic
        feat1, feat2 = pair['feature1'], pair['feature2']
        if feat1 in DERIVED_FEATURES and feat2 in RAW_NUM_FEATURES:
            recommendation = f"Consider dropping {feat1} (derived feature)"
        elif feat2 in DERIVED_FEATURES and feat1 in RAW_NUM_FEATURES:
            recommendation = f"Consider dropping {feat2} (derived feature)"
        elif feat1 == TARGET_COL:
            recommendation = f"Keep {feat2} (strong predictor)"
        elif feat2 == TARGET_COL:
            recommendation = f"Keep {feat1} (strong predictor)"
        else:
            recommendation = "Domain knowledge needed for decision"
        
        print(f"{feat1} <-> {feat2}: {recommendation}")
else:
    print("\nNo highly correlated feature pairs detected")

# Summary statistics
print("\nCORRELATION SUMMARY:")
print(f"Features analyzed: {len(corr_features)}")
print(f"Total correlation pairs: {len(corr_features) * (len(corr_features) - 1) // 2}")
print(f"High Pearson correlations (>0.9): {len(pearson_high)}")
print(f"High Spearman correlations (>0.9): {len(spearman_high)}")

=== CORRELATION & MULTICOLLINEARITY ANALYSIS ===
Correlation matrices calculated:
Pearson correlation shape: (11, 11)
Spearman correlation shape: (11, 11)

HIGH CORRELATIONS (|ρ| > 0.9):

Pearson correlations > 0.9:
Age             <-> Age_x_BodyTemp  |  0.998
Heart_Rate      <-> HeatStressIdx   |  0.996
Duration        <-> HRxDur          |  0.994
HRxDur          <-> Calories        |  0.977
Duration        <-> Calories        |  0.960
Height          <-> Weight          |  0.958
HRxDur          <-> HeatStressIdx   |  0.929
HeatStressIdx   <-> Calories        |  0.925
Heart_Rate      <-> Calories        |  0.909
Heart_Rate      <-> HRxDur          |  0.906
Duration        <-> HeatStressIdx   |  0.906
Duration        <-> Body_Temp       |  0.903

Spearman correlations > 0.9:
Age             <-> Age_x_BodyTemp  |  0.999
Duration        <-> HRxDur          |  0.997
Heart_Rate      <-> HeatStressIdx   |  0.996
HRxDur          <-> Calories        |  0.988
Duration        <-> Calories      